In [23]:
import pandas as pd
import numpy as np

# Load the dataset
df = pd.read_csv(r'C:\Users\tiwar\OneDrive\Desktop\forgefocus\dataset.csv')

# Combine date and time into a single datetime column
df['Timestamp'] = pd.to_datetime(df['LastUpdatedDate'] + ' ' + df['LastUpdatedTime'], format='%d-%m-%Y %H:%M:%S')

# Drop original date/time if not needed
df.drop(['LastUpdatedDate', 'LastUpdatedTime'], axis=1, inplace=True)

# Sort by time for proper trend visualization
df.sort_values(by='Timestamp', inplace=True)

# Reset index
df.reset_index(drop=True, inplace=True)


In [24]:
# Add occupancy ratio
df['OccupancyRate'] = df['Occupancy'] / df['Capacity']


In [25]:
# Simple linear pricing logic
def calculate_baseline_price(row, base_price=10):
    return round(base_price * (1 + row['OccupancyRate']), 2)

# Apply to data
df['BaselinePrice'] = df.apply(calculate_baseline_price, axis=1)


In [26]:
# View key columns
df[['Timestamp', 'Occupancy', 'Capacity', 'OccupancyRate', 'BaselinePrice']].head()


Timestamp  Occupancy  Capacity  OccupancyRate  BaselinePrice
0 2016-10-04 07:59:00         61       577       0.105719          11.06
1 2016-10-04 07:59:00        237      1200       0.197500          11.97
2 2016-10-04 07:59:00        264       687       0.384279          13.84
3 2016-10-04 07:59:00        249       485       0.513402          15.13
4 2016-10-04 07:59:00        614      1920       0.319792          13.20

In [27]:
# Map traffic condition to numerical values
traffic_map = {'low': 1, 'average': 2, 'high': 3}
df['TrafficScore'] = df['TrafficConditionNearby'].map(traffic_map)

# Map vehicle type (arbitrary weights based on size/demand potential)
vehicle_map = {'cycle': 0.5, 'bike': 1, 'car': 2, 'truck': 3}
df['VehicleWeight'] = df['VehicleType'].map(vehicle_map)

# Normalize all features to [0, 1]
df['Norm_OccupancyRate'] = df['OccupancyRate']
df['Norm_QueueLength'] = df['QueueLength'] / df['QueueLength'].max()
df['Norm_Traffic'] = df['TrafficScore'] / 3
df['Norm_VehicleWeight'] = df['VehicleWeight'] / 3
df['Norm_SpecialDay'] = df['IsSpecialDay']  # already 0/1


In [28]:
feature_cols = [
    'Norm_OccupancyRate',
    'Norm_QueueLength',
    'Norm_Traffic',
    'Norm_VehicleWeight',
    'Norm_SpecialDay'
]

df['DemandScore'] = df[feature_cols].mean(axis=1)


In [29]:
def demand_to_price(score, min_price=5, max_price=20):
    return round(min_price + (max_price - min_price) * score, 2)

df['Model2_Price'] = df['DemandScore'].apply(demand_to_price)


In [30]:
df[['Timestamp', 'DemandScore', 'Model2_Price']].head()


Timestamp  DemandScore  Model2_Price
0 2016-10-04 07:59:00     0.234477          8.52
1 2016-10-04 07:59:00     0.199500          7.99
2 2016-10-04 07:59:00     0.303523          9.55
3 2016-10-04 07:59:00     0.329347          9.94
4 2016-10-04 07:59:00     0.190625          7.86

In [31]:
# Simulate 3 competitor lots with lat/long and mock prices
competitors = pd.DataFrame({
    'CompetitorID': ['Lot_A', 'Lot_B', 'Lot_C'],
    'Latitude': [26.1450, 26.1442, 26.1460],
    'Longitude': [91.7366, 91.7370, 91.7350],
    'CurrentPrice': [11.0, 14.5, 9.0]  # Assume these are current live prices
})


In [32]:
def haversine_distance(lat1, lon1, lat2, lon2):
    # Approximate distance between two lat/lon points in km
    R = 6371  # Earth radius in km
    lat1, lon1, lat2, lon2 = map(np.radians, [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = np.sin(dlat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2)**2
    return R * 2 * np.arcsin(np.sqrt(a))

# Your lot's location
my_lat = df['Latitude'].iloc[0]
my_lon = df['Longitude'].iloc[0]

# Compute distance from your lot to competitors
competitors['Distance_km'] = competitors.apply(
    lambda row: haversine_distance(my_lat, my_lon, row['Latitude'], row['Longitude']), axis=1
)

# Find nearest competitor
closest = competitors.loc[competitors['Distance_km'].idxmin()]


In [33]:
def adjust_price_competitively(own_price, competitor_price, factor=0.9):
    # Discount slightly if competitor is cheaper
    if competitor_price < own_price:
        return round(competitor_price * factor, 2)
    return own_price

df['Model3_Price'] = df.apply(
    lambda row: adjust_price_competitively(row['Model2_Price'], closest['CurrentPrice']),
    axis=1
)


In [34]:
df[['Timestamp', 'BaselinePrice', 'Model2_Price', 'Model3_Price']].tail()


Timestamp  BaselinePrice  Model2_Price  Model3_Price
18363 2016-12-19 16:30:00          17.94         10.78         10.78
18364 2016-12-19 16:30:00          20.00         11.40          9.90
18365 2016-12-19 16:30:00          13.34          7.90          7.90
18366 2016-12-19 16:30:00          15.39         10.22         10.22
18367 2016-12-19 16:30:00          16.15         10.24         10.24

In [35]:
%pip install pathway
import pathway as pw
import pandas as pd

Note: you may need to restart the kernel to use updated packages.


In [36]:
from dataclasses import dataclass
from datetime import datetime

@dataclass
class ParkingSchema:
    Timestamp: datetime
    Occupancy: int
    Capacity: int
    QueueLength: int
    TrafficConditionNearby: str
    VehicleType: str
    IsSpecialDay: int

In [37]:
# Read CSV using pandas (already done in cell 0 as df)
# df = pd.read_csv(r"C:\Users\tiwar\OneDrive\Desktop\forgefocus\dataset.csv")

# Write DataFrame to CSV (for example, after processing)
try:
	df.to_csv(r"C:\Users\tiwar\OneDrive\Desktop\forgefocus\dataset.csv", index=False)
except NameError:
	print("DataFrame 'df' is not defined. Please run the cell where 'df' is created.")

In [38]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource

In [39]:
output_notebook()

Loading BokehJS ...

In [40]:
try:
	source = ColumnDataSource(df)
except NameError:
	print("DataFrame 'df' is not defined. Please run the cell where 'df' is created.")

In [41]:
try:
	source
except NameError:
	source = ColumnDataSource(df)

p = figure(x_axis_type="datetime", title="Parking Lot Pricing", width=800, height=400)
p.line(x='Timestamp', y='BaselinePrice', source=source, color='green', legend_label="Model 1")
p.line(x='Timestamp', y='Model2_Price', source=source, color='blue', legend_label="Model 2")
p.line(x='Timestamp', y='Model3_Price', source=source, color='red', legend_label="Model 3")

p.legend.location = "top_left"
p.xaxis.axis_label = "Time"
p.yaxis.axis_label = "Price ($)"
show(p)

In [47]:
%pip install pathway
import pathway as pw
from datetime import datetime

  Using cached pathway-0.post1-py3-none-any.whl.metadata (1.3 kB)
Using cached pathway-0.post1-py3-none-any.whl (2.8 kB)
Note: you may need to restart the kernel to use updated packages.


In [49]:
# The real Pathway package does not provide pw.Schema.
# Use a dataclass for schema definition as shown previously.

from dataclasses import dataclass
from datetime import datetime

@dataclass
class ParkingSchema:
    Timestamp: datetime
    Occupancy: int
    Capacity: int
    QueueLength: int
    VehicleType: str
    TrafficConditionNearby: str
    IsSpecialDay: int

In [53]:
# Pathway streaming API is not available on Windows.
# Continue using pandas for CSV processing.

# If you want to reload the CSV:
df = pd.read_csv(r"C:\Users\tiwar\OneDrive\Desktop\forgefocus\dataset.csv")
df.head()

ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy  \
0      0      BHMBCCMKT01       577  26.144536  91.736172         61   
1   5248      BHMNCPHST01      1200  26.140014  91.731000        237   
2   3936      BHMMBMMBX01       687  20.000035  78.000003        264   
3   6560      BHMNCPNST01       485  26.140048  91.730972        249   
4  17056         Shopping      1920  26.150504  91.733531        614   

  VehicleType TrafficConditionNearby  QueueLength  IsSpecialDay  ...  \
0         car                    low            1             0  ...   
1        bike                    low            2             0  ...   
2         car                    low            2             0  ...   
3         car                    low            2             0  ...   
4       cycle                    low            2             0  ...   

  TrafficScore  VehicleWeight  Norm_OccupancyRate  Norm_QueueLength  \
0            1            2.0            0.105719          0.066667   
1            1            1.0            0.197500          0.133333   
2            1            2.0            0.384279          0.133333   
3            1            2.0            0.513402          0.133333   
4            1            0.5            0.319792          0.133333   

   Norm_Traffic  Norm_VehicleWeight  Norm_SpecialDay  DemandScore  \
0      0.333333            0.666667                0     0.234477   
1      0.333333            0.333333                0     0.199500   
2      0.333333            0.666667                0     0.303523   
3      0.333333            0.666667                0     0.329347   
4      0.333333            0.166667                0     0.190625   

   Model2_Price  Model3_Price  
0          8.52          8.52  
1          7.99          7.99  
2          9.55          9.55  
3          9.94          9.94  
4          7.86          7.86  

[5 rows x 23 columns]

In [54]:
def compute_price_logic(row):
    occupancy_rate = row.Occupancy / row.Capacity
    traffic = {'low': 1, 'average': 2, 'high': 3}.get(row.TrafficConditionNearby, 2)
    vehicle_weight = {'cycle': 0.5, 'bike': 1, 'car': 2, 'truck': 3}.get(row.VehicleType, 2)

    norm_occ = occupancy_rate
    norm_queue = row.QueueLength / 10
    norm_traffic = traffic / 3
    norm_vehicle = vehicle_weight / 3
    norm_special = row.IsSpecialDay

    demand_score = (norm_occ + norm_queue + norm_traffic + norm_vehicle + norm_special) / 5
    model2_price = 5 + (20 - 5) * demand_score

    competitor_price = 12  # Placeholder
    model3_price = min(model2_price, competitor_price * 0.9)

    return {"Model2_Price": round(model2_price, 2), "Model3_Price": round(model3_price, 2)}

# Apply transformation

In [55]:
# Apply compute_price_logic to each row and create a DataFrame from the results
result = df.apply(compute_price_logic, axis=1, result_type='expand')

# Optionally, join the result with the original DataFrame if you want to keep all columns
df_with_prices = pd.concat([df, result], axis=1)

# Write the result to CSV
df_with_prices.to_csv(r"C:\Users\tiwar\OneDrive\Desktop\forgefocus\dataset.csv", index=False)

In [57]:
# Bokeh and ColumnDataSource are already imported and output_notebook() already called in previous cells

# Use the already processed df and source
# df already has 'Timestamp' column in correct format

p = figure(x_axis_type="datetime", title="Dynamic Parking Prices", height=400, width=900)
p.line(x='Timestamp', y='BaselinePrice', source=source, line_color='green', legend_label='Model 1')
p.line(x='Timestamp', y='Model2_Price', source=source, line_color='blue', legend_label='Model 2')
p.line(x='Timestamp', y='Model3_Price', source=source, line_color='red', legend_label='Model 3')
p.legend.location = "top_left"
p.xaxis.axis_label = 'Time'
p.yaxis.axis_label = 'Price ($)'
show(p)


In [60]:
# Remove duplicate columns by keeping the first occurrence
df_with_prices = df_with_prices.loc[:, ~df_with_prices.columns.duplicated()]

df_with_prices['Price_Change'] = df_with_prices['Model3_Price'].diff()

# Flag drastic changes
df_with_prices['Anomaly'] = df_with_prices['Price_Change'].abs() > 5  # Tunable threshold


In [62]:
df_with_prices['Revenue'] = df_with_prices['Model3_Price'] * df_with_prices['Occupancy']
peak_slot = df_with_prices.loc[df_with_prices['Revenue'].idxmax()]


In [64]:
optimal_slots = df_with_prices[(df_with_prices['Model3_Price'] > 8) & (df_with_prices['Model3_Price'] < 15)]
best_time = optimal_slots.sort_values(by='Occupancy', ascending=False).head(1)
